In [1]:
import gc
import os
from pathlib import Path
import random
import sys

from tqdm.notebook import tqdm
import numpy as np
import pandas as pd
import scipy as sp


import matplotlib.pyplot as plt
import seaborn as sns

from IPython.core.display import display, HTML

# --- plotly ---
from plotly import tools, subplots
import plotly.offline as py
py.init_notebook_mode(connected=True)
import plotly.graph_objs as go
import plotly.express as px
import plotly.figure_factory as ff
import plotly.io as pio
pio.templates.default = "plotly_dark"

# --- models ---
from sklearn import preprocessing
from sklearn.model_selection import KFold
import lightgbm as lgb
import xgboost as xgb
import catboost as cb

# --- setup ---
pd.set_option('max_columns', 50)

In [2]:

df = pd.read_csv('https://www.gstatic.com/covid19/mobility/Global_Mobility_Report.csv')
df

/opt/conda/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3156: DtypeWarning:

Columns (4,5) have mixed types.Specify dtype option on import or set low_memory=False.



country_region_code        country_region       sub_region_1  \
0                        AE  United Arab Emirates                NaN   
1                        AE  United Arab Emirates                NaN   
2                        AE  United Arab Emirates                NaN   
3                        AE  United Arab Emirates                NaN   
4                        AE  United Arab Emirates                NaN   
...                     ...                   ...                ...   
4973947                  ZW              Zimbabwe  Midlands Province   
4973948                  ZW              Zimbabwe  Midlands Province   
4973949                  ZW              Zimbabwe  Midlands Province   
4973950                  ZW              Zimbabwe  Midlands Province   
4973951                  ZW              Zimbabwe  Midlands Province   

        sub_region_2 metro_area iso_3166_2_code  census_fips_code  \
0                NaN        NaN             NaN               NaN   
1                NaN        NaN             NaN               NaN   
2                NaN        NaN             NaN               NaN   
3                NaN        NaN             NaN               NaN   
4                NaN        NaN             NaN               NaN   
...              ...        ...             ...               ...   
4973947       Kwekwe        NaN             NaN               NaN   
4973948       Kwekwe        NaN             NaN               NaN   
4973949       Kwekwe        NaN             NaN               NaN   
4973950       Kwekwe        NaN             NaN               NaN   
4973951       Kwekwe        NaN             NaN               NaN   

                            place_id        date  \
0        ChIJvRKrsd9IXj4RpwoIwFYv0zM  2020-02-15   
1        ChIJvRKrsd9IXj4RpwoIwFYv0zM  2020-02-16   
2        ChIJvRKrsd9IXj4RpwoIwFYv0zM  2020-02-17   
3        ChIJvRKrsd9IXj4RpwoIwFYv0zM  2020-02-18   
4        ChIJvRKrsd9IXj4RpwoIwFYv0zM  2020-02-19   
...                              ...         ...   
4973947  ChIJRcIZ3-FJNBkRRsj55IcLpfU  2021-04-05   
4973948  ChIJRcIZ3-FJNBkRRsj55IcLpfU  2021-04-06   
4973949  ChIJRcIZ3-FJNBkRRsj55IcLpfU  2021-04-07   
4973950  ChIJRcIZ3-FJNBkRRsj55IcLpfU  2021-04-08   
4973951  ChIJRcIZ3-FJNBkRRsj55IcLpfU  2021-04-09   

         retail_and_recreation_percent_change_from_baseline  \
0                                                      0.0    
1                                                      1.0    
2                                                     -1.0    
3                                                     -2.0    
4                                                     -2.0    
...                                                    ...    
4973947                                                NaN    
4973948                                                NaN    
4973949                                                NaN    
4973950                                                NaN    
4973951                                                NaN    

         grocery_and_pharmacy_percent_change_from_baseline  \
0                                                      4.0   
1                                                      4.0   
2                                                      1.0   
3                                                      1.0   
4                                                      0.0   
...                                                    ...   
4973947                                                NaN   
4973948                                                NaN   
4973949                                                NaN   
4973950                                                NaN   
4973951                                                NaN   

         parks_percent_change_from_baseline  \
0                                       5.0   
1                                       4.0   
2                                       5.0   

In [3]:
europe_country_list =list([
    'Austria','Belgium','Bulgaria','Croatia','Cyprus','Czechia','Denmark','Estonia','Finland','France','Germany','Greece','Hungary','Ireland',
    'Italy', 'Latvia','Luxembourg','Lithuania','Malta','Norway','Netherlands','Poland','Portugal','Romania','Slovakia','Slovenia',
    'Spain', 'Sweden', 'United Kingdom', 'Iceland', 'Russia', 'Switzerland', 'Serbia', 'Ukraine', 'Belarus',
    'Albania', 'Bosnia and Herzegovina', 'Kosovo', 'Moldova', 'Montenegro', 'North Macedonia'])

In [4]:
df = df[df['country_region'].isin(europe_country_list)]
df.shape

(1335688, 15)

In [5]:
df

country_region_code country_region sub_region_1 sub_region_2  \
182462                   AT        Austria          NaN          NaN   
182463                   AT        Austria          NaN          NaN   
182464                   AT        Austria          NaN          NaN   
182465                   AT        Austria          NaN          NaN   
182466                   AT        Austria          NaN          NaN   
...                     ...            ...          ...          ...   
3841545                  UA        Ukraine          NaN          NaN   
3841546                  UA        Ukraine          NaN          NaN   
3841547                  UA        Ukraine          NaN          NaN   
3841548                  UA        Ukraine          NaN          NaN   
3841549                  UA        Ukraine          NaN          NaN   

                     metro_area iso_3166_2_code  census_fips_code  \
182462                      NaN             NaN               NaN   
182463                      NaN             NaN               NaN   
182464                      NaN             NaN               NaN   
182465                      NaN             NaN               NaN   
182466                      NaN             NaN               NaN   
...                         ...             ...               ...   
3841545  Kiev Metropolitan Area             NaN               NaN   
3841546  Kiev Metropolitan Area             NaN               NaN   
3841547  Kiev Metropolitan Area             NaN               NaN   
3841548  Kiev Metropolitan Area             NaN               NaN   
3841549  Kiev Metropolitan Area             NaN               NaN   

                            place_id        date  \
182462   ChIJfyqdJZsHbUcRr8Hk3XvUEhA  2020-02-15   
182463   ChIJfyqdJZsHbUcRr8Hk3XvUEhA  2020-02-16   
182464   ChIJfyqdJZsHbUcRr8Hk3XvUEhA  2020-02-17   
182465   ChIJfyqdJZsHbUcRr8Hk3XvUEhA  2020-02-18   
182466   ChIJfyqdJZsHbUcRr8Hk3XvUEhA  2020-02-19   
...                              ...         ...   
3841545  ChIJzYwQhKf_1EAR5PjP6COXiNw  2021-04-07   
3841546  ChIJzYwQhKf_1EAR5PjP6COXiNw  2021-04-08   
3841547  ChIJzYwQhKf_1EAR5PjP6COXiNw  2021-04-09   
3841548  ChIJzYwQhKf_1EAR5PjP6COXiNw  2021-04-10   
3841549  ChIJzYwQhKf_1EAR5PjP6COXiNw  2021-04-11   

         retail_and_recreation_percent_change_from_baseline  \
182462                                                 9.0    
182463                                                15.0    
182464                                                 9.0    
182465                                                 8.0    
182466                                                 4.0    
...                                                    ...    
3841545                                              -46.0    
3841546                                              -39.0    
3841547                                              -38.0    
3841548                                              -39.0    
3841549                                              -38.0    

         grocery_and_pharmacy_percent_change_from_baseline  \
182462                                                 1.0   
182463                                                21.0   
182464                                                 5.0   
182465                                                 5.0   
182466                                                 2.0   
...                                                    ...   
3841545                                               -6.0   
3841546                                                2.0   
3841547                                                3.0   
3841548                                                2.0   
3841549                                                2.0   

         parks_percent_change_from_baseline  \
182462                                 42.0   
182463                                 42.0   
182464                                 35.0   

In [6]:
df = df.drop(['sub_region_1', 'sub_region_2', 'country_region_code', 'sub_region_2', 'metro_area',
              'iso_3166_2_code', 'census_fips_code', 'place_id'], axis = 1)
df

country_region        date  \
182462         Austria  2020-02-15   
182463         Austria  2020-02-16   
182464         Austria  2020-02-17   
182465         Austria  2020-02-18   
182466         Austria  2020-02-19   
...                ...         ...   
3841545        Ukraine  2021-04-07   
3841546        Ukraine  2021-04-08   
3841547        Ukraine  2021-04-09   
3841548        Ukraine  2021-04-10   
3841549        Ukraine  2021-04-11   

         retail_and_recreation_percent_change_from_baseline  \
182462                                                 9.0    
182463                                                15.0    
182464                                                 9.0    
182465                                                 8.0    
182466                                                 4.0    
...                                                    ...    
3841545                                              -46.0    
3841546                                              -39.0    
3841547                                              -38.0    
3841548                                              -39.0    
3841549                                              -38.0    

         grocery_and_pharmacy_percent_change_from_baseline  \
182462                                                 1.0   
182463                                                21.0   
182464                                                 5.0   
182465                                                 5.0   
182466                                                 2.0   
...                                                    ...   
3841545                                               -6.0   
3841546                                                2.0   
3841547                                                3.0   
3841548                                                2.0   
3841549                                                2.0   

         parks_percent_change_from_baseline  \
182462                                 42.0   
182463                                 42.0   
182464                                 35.0   
182465                                 40.0   
182466                                 10.0   
...                                     ...   
3841545                               -34.0   
3841546                                -3.0   
3841547                                 8.0   
3841548                                39.0   
3841549                                53.0   

         transit_stations_percent_change_from_baseline  \
182462                                            13.0   
182463                                            12.0   
182464                                             3.0   
182465                                             2.0   
182466                                            -1.0   
...                                                ...   
3841545                                          -46.0   
3841546                                          -39.0   
3841547                                          -38.0   
3841548                                          -32.0   
3841549                                          -27.0   

         workplaces_percent_change_from_baseline  \
182462                                       0.0   
182463                                       1.0   
182464                                      -4.0   
182465                                      -4.0   
182466                                      -5.0   
...                                          ...   
3841545                                    -44.0   
3841546                                    -42.0   
3841547                                    -41.0   
3841548                                    -22.0   
3841549                                    -17.0   

         residential_percent_change_from_baseline  
182462                                       -2.0  
182463                                       -2.0  
182464

In [7]:
df = df.groupby(['date', 'country_region']).sum()

In [8]:
df

retail_and_recreation_percent_change_from_baseline  \
date       country_region                                                               
2020-02-15 Austria                                                             704.0    
           Belarus                                                              10.0    
           Belgium                                                              44.0    
           Bosnia and Herzegovina                                                8.0    
           Bulgaria                                                           -145.0    
...                                                                              ...    
2021-04-11 Spain                                                             -2563.0    
           Sweden                                                            -1777.0    
           Switzerland                                                        -877.0    
           Ukraine                                                             -63.0    
           United Kingdom                                                   -20365.0    

                                   grocery_and_pharmacy_percent_change_from_baseline  \
date       country_region                                                              
2020-02-15 Austria                                                              88.0   
           Belarus                                                               9.0   
           Belgium                                                              15.0   
           Bosnia and Herzegovina                                                6.0   
           Bulgaria                                                             15.0   
...                                                                              ...   
2021-04-11 Spain                                                                79.0   
           Sweden                                                             -780.0   
           Switzerland                                                           1.0   
           Ukraine                                                               6.0   
           United Kingdom                                                    -2738.0   

                                   parks_percent_change_from_baseline  \
date       country_region                                               
2020-02-15 Austria                                             1536.0   
           Belarus                                               21.0   
           Belgium                                              328.0   
           Bosnia and Herzegovina                                16.0   
           Bulgaria                                            -959.0   
...                                                               ...   
2021-04-11 Spain                                              -1388.0   
           Sweden                                               -76.0   
           Switzerland                                         1096.0   
           Ukraine                                               81.0   
           United Kingdom                                     17169.0   

                                   transit_stations_percent_change_from_baseline  \
date       country_region                                                          
2020-02-15 Austria                                                        1058.0   
           Belarus                                                          11.0   
           Belgium                                                         104.0   
           Bosnia and Herzegovina                                            3.0   
           Bulgaria                                                        -29.0   
...                                                                          ...   
2021-04-11 Spain                                                         -1997.0   
           Sweden         

In [9]:
df.reset_index(inplace=True)
df

date          country_region  \
0      2020-02-15                 Austria   
1      2020-02-15                 Belarus   
2      2020-02-15                 Belgium   
3      2020-02-15  Bosnia and Herzegovina   
4      2020-02-15                Bulgaria   
...           ...                     ...   
15142  2021-04-11                   Spain   
15143  2021-04-11                  Sweden   
15144  2021-04-11             Switzerland   
15145  2021-04-11                 Ukraine   
15146  2021-04-11          United Kingdom   

       retail_and_recreation_percent_change_from_baseline  \
0                                                  704.0    
1                                                   10.0    
2                                                   44.0    
3                                                    8.0    
4                                                 -145.0    
...                                                  ...    
15142                                            -2563.0    
15143                                            -1777.0    
15144                                             -877.0    
15145                                              -63.0    
15146                                           -20365.0    

       grocery_and_pharmacy_percent_change_from_baseline  \
0                                                   88.0   
1                                                    9.0   
2                                                   15.0   
3                                                    6.0   
4                                                   15.0   
...                                                  ...   
15142                                               79.0   
15143                                             -780.0   
15144                                                1.0   
15145                                                6.0   
15146                                            -2738.0   

       parks_percent_change_from_baseline  \
0                                  1536.0   
1                                    21.0   
2                                   328.0   
3                                    16.0   
4                                  -959.0   
...                                   ...   
15142                             -1388.0   
15143                               -76.0   
15144                              1096.0   
15145                                81.0   
15146                             17169.0   

       transit_stations_percent_change_from_baseline  \
0                                             1058.0   
1                                               11.0   
2                                              104.0   
3                                                3.0   
4                                              -29.0   
...                                              ...   
15142                                        -1997.0   
15143                                        -4867.0   
15144                                         -420.0   
15145                                          -39.0   
15146                                       -15921.0   

       workplaces_percent_change_from_baseline  \
0                                        -41.0   
1                                          4.0   
2                                         15.0   
3                                          1.0   
4                                        -69.0   
...                                        ...   
15142                                  -1011.0   
15143                                   -547.0   
15144                                   -274.0   
15145                                    -36.0   
15146                                  -6797.0   

       residential_percent_change_from_baseline  
0                                         -74.0  
1                                          -1.0  
2                                         -12.0  
3  

In [10]:
fig = px.line(df, x="date", y="retail_and_recreation_percent_change_from_baseline", color='country_region', 
              title="retail_and_recreation_percent_change_from_baseline")
fig.show()

In [11]:
df_all = df.groupby(['date']).sum()
df_all.reset_index(inplace=True)
df_all

date  retail_and_recreation_percent_change_from_baseline  \
0    2020-02-15                                             5361.0    
1    2020-02-16                                             4779.0    
2    2020-02-17                                            10328.0    
3    2020-02-18                                            12544.0    
4    2020-02-19                                             9294.0    
..          ...                                                ...    
417  2021-04-07                                           -70086.0    
418  2021-04-08                                           -67164.0    
419  2021-04-09                                           -73057.0    
420  2021-04-10                                           -84922.0    
421  2021-04-11                                           -74736.0    

     grocery_and_pharmacy_percent_change_from_baseline  \
0                                                634.0   
1                                              -1266.0   
2                                               5024.0   
3                                               4393.0   
4                                               2225.0   
..                                                 ...   
417                                             6342.0   
418                                            12052.0   
419                                            14926.0   
420                                             5597.0   
421                                            -4806.0   

     parks_percent_change_from_baseline  \
0                               10171.0   
1                               -3431.0   
2                               20690.0   
3                               25474.0   
4                               15443.0   
..                                  ...   
417                             10460.0   
418                             23146.0   
419                             26219.0   
420                             21187.0   
421                             44049.0   

     transit_stations_percent_change_from_baseline  \
0                                           8380.0   
1                                           4841.0   
2                                           1476.0   
3                                             74.0   
4                                          -2305.0   
..                                             ...   
417                                       -73897.0   
418                                       -73486.0   
419                                       -72329.0   
420                                       -61781.0   
421                                       -55867.0   

     workplaces_percent_change_from_baseline  \
0                                     -648.0   
1                                    -2152.0   
2                                   -10400.0   
3                                   -15749.0   
4                                   -16340.0   
..                                       ...   
417                                -103875.0   
418                                -100591.0   
419                                 -88266.0   
420                                 -26513.0   
421                                 -25392.0   

     residential_percent_change_from_baseline  
0                                      -135.0  
1                                      -273.0  
2                                      2062.0  
3                                      2363.0  
4                                      1940.0  
..                                        ...  
417                                   28084.0  
418                                   27989.0  
419                                   26708.0  
420                                   11444.0  
421                                    7738.0  

[422 rows x 7 columns]

In [12]:
fig = px.line(df_all, x="date", y="retail_and_recreation_percent_change_from_baseline", 
              title="Europe retail_and_recreation_percent_change_from_baseline")
fig.show()

In [13]:
fig = px.line(df, x="date", y="grocery_and_pharmacy_percent_change_from_baseline", color='country_region', 
              title="grocery_and_pharmacy_percent_change_from_baseline")
fig.show()

In [14]:
fig = px.line(df_all, x="date", y="grocery_and_pharmacy_percent_change_from_baseline", 
              title="Europe grocery_and_pharmacy_percent_change_from_baseline")
fig.show()

In [15]:
fig = px.line(df, x="date", y="parks_percent_change_from_baseline", color='country_region', 
              title="parks_percent_change_from_baseline")
fig.show()

In [16]:
fig = px.line(df_all, x="date", y="parks_percent_change_from_baseline", 
              title="Europe parks_percent_change_from_baseline")
fig.show()

In [17]:
fig = px.line(df, x="date", y="transit_stations_percent_change_from_baseline", color='country_region', 
              title="transit_stations_percent_change_from_baseline")
fig.show()

In [18]:
fig = px.line(df_all, x="date", y="transit_stations_percent_change_from_baseline", 
              title="Europe transit_stations_percent_change_from_baseline")
fig.show()

In [19]:
fig = px.line(df, x="date", y="workplaces_percent_change_from_baseline", color='country_region', 
              title="workplaces_percent_change_from_baseline")
fig.show()

In [20]:
fig = px.line(df_all, x="date", y="workplaces_percent_change_from_baseline", 
              title="Europe workplaces_percent_change_from_baseline")
fig.show()

In [21]:
fig = px.line(df, x="date", y="residential_percent_change_from_baseline", color='country_region', 
              title="residential_percent_change_from_baseline")
fig.show()

In [22]:
fig = px.line(df_all, x="date", y="residential_percent_change_from_baseline", 
              title="Europe residential_percent_change_from_baseline")
fig.show()